# Exploration des résultats des 302

In [1]:
import sqlite3
import pandas as pd
import numpy as np
from math import ceil
import seaborn as sns
import matplotlib.pyplot as plt
%matplotlib inline
from pprint import pprint

In [2]:
db = "recopytex.db"
conn = sqlite3.connect(db)
c = conn.cursor()

In [3]:
tribe_name = "302"

Id de la classe de 302

In [4]:
tribe_id = c.execute("SELECT id from tribe WHERE tribe.name ==  ?", (tribe_name,)).fetchone()[0]

In [5]:
print(tribe_id)

1


Evaluations disponibles

In [6]:
evals = c.execute("SELECT id, name from eval WHERE eval.tribe_id == ?", (tribe_id,))

In [7]:
evals.fetchmany()

[(1, 'DS1 mise en jambe')]

## DS 1 mise en jambre

In [8]:
eval_id = 1

In [9]:
questions_scores = pd.read_sql_query("SELECT \
                student.name as name,\
                student.surname as surname,\
                score.value as value, \
                question.competence as competence,\
                question.name as question,\
                exercise.name as exercise, \
                eval.name as eval\
                FROM score\
                JOIN question ON score.question_id==question.id \
                JOIN exercise ON question.exercise_id==exercise.id \
                JOIN eval ON exercise.eval_id==eval.id \
                JOIN student ON score.student_id==student.id\
                WHERE eval.id == (?)",
                 conn,
                params = (eval_id,))

On efface les lignes sans "value"

In [10]:
questions_scores = questions_scores[questions_scores["value"]!='']

On transforme les "value" en score

In [11]:
def note2score(x):
    if x["value"] == '.':
        return 0
    if x["value"] not in [0, 1, 2, 3]:
        raise ValueError(f"The evaluation is out of range: {x['value']} at {x}")
    return x["value"]

In [12]:
questions_scores["score"] = questions_scores.apply(note2score, axis=1)

In [13]:
#questions_scores.head()

Nom des élèves en entier

In [14]:
questions_scores["fullname"] = questions_scores["name"] + " " + questions_scores["surname"]

Nom des compétences en entier

In [15]:
def competence_fullname(x):
    competences = {
        "Cher": "Chercher",
        "Mod": "Modéliser",
        "Rep": "Représenter",
        "Rai": "Raisonner",
        "Cal": "Calculer",
        "Com": "Communiquer",
        "Con": "Connaître"
    }
    try:
        return competences[x['competence']]
    except KeyError:
        return ""

In [16]:
questions_scores["abv_competence"] = questions_scores["competence"]
questions_scores["competence"] = questions_scores.apply(competence_fullname, axis=1)

In [17]:
def score_mean(x):
    mean = np.mean(x)
    return round(mean, 0)

score_mean.__name__ = "Moyenne discrète"

In [18]:
report_comp = pd.pivot_table(questions_scores,
              index=["fullname"],
              columns = ['competence'],
              values = ["score"],
              aggfunc = [score_mean])

Applatissement du nom des colonnes

In [19]:
report_comp.columns = report_comp.columns.levels[-1]

In [20]:
report_comp.head(questions_scores)

TypeError: cannot do slice indexing on <class 'pandas.core.indexes.base.Index'> with these indexers [                  name      surname value   competence question  \
0     ABDALLAH ALLAOUI    Taiassima     2     Chercher        1   
1     ABDALLAH ALLAOUI    Taiassima     2     Calculer        2   
2     ABDALLAH ALLAOUI    Taiassima     .     Calculer      2.c   
3                ADANI        Ismou     2     Chercher        1   
4                ADANI        Ismou     2     Calculer        2   
5                ADANI        Ismou     1     Calculer      2.c   
6              AHAMADA   Dhoulkamal     3     Chercher        1   
7              AHAMADA   Dhoulkamal     0     Calculer        2   
8              AHAMADA   Dhoulkamal     0     Calculer      2.c   
9              AHAMADI     Asbahati     3     Chercher        1   
10             AHAMADI     Asbahati     3     Calculer        2   
11             AHAMADI     Asbahati     0     Calculer      2.c   
12     AHAMADI OUSSENI  Ansu

Heapmap des competences et des élèves

In [ ]:
plt.figure(figsize=(10, 10))
ax = sns.heatmap(report_comp, cmap='YlOrRd', linewidths=.5)
ax.tick_params(labelbottom='on',labeltop='on')